In [1]:
# Eric's modification
import os
import torch
import numpy as np
os.environ['CUDA_VISIBLE_DEVICES'] = '2'
from torch.utils.data import TensorDataset, DataLoader, Subset
import torchvision
from torch.utils.tensorboard import SummaryWriter
writer = SummaryWriter()
from datetime import datetime
print(datetime.now().strftime("%Y-%m-%d %H:%M:%S"))
from torch.utils.data import TensorDataset, DataLoader, Subset
#import torchvision
from os import path

from src.utils import *
from src.models import *
from src.methods import *

data_path = os.path.join(os.getcwd(), 'project_data/')
print(data_path)

USE_GPU = True
if USE_GPU and torch.cuda.is_available():
    device = torch.device('cuda')
else:
    device = torch.device('cpu')
print(device)

2024-03-14 19:43:49
/home/banyh2000/ECE247-Group-Project/project_data/
cuda


In [2]:
X_test = np.load(data_path+"X_test.npy")
y_test = np.load(data_path+"y_test.npy")
person_train_valid = np.load(data_path+"person_train_valid.npy")
X_train_valid = np.load(data_path+"X_train_valid.npy")
y_train_valid = np.load(data_path+"y_train_valid.npy")
person_test = np.load(data_path+"person_test.npy")
#:\Users\pluto\Desktop\2024_winter\ECE_147\final_project\ECE247-Group-Project\src\project_data\y_test.npy

In [3]:
X_test = np.load(data_path + "X_test.npy")
y_test = np.load(data_path + "y_test.npy") - 769
person_train_valid = np.load(data_path + "person_train_valid.npy")
X_train_valid = np.load(data_path + "X_train_valid.npy")
y_train_valid = np.load(data_path + "y_train_valid.npy") - 769
person_test = np.load(data_path + "person_test.npy")

In [4]:
print ('Training/Valid data shape: {}'.format(X_train_valid.shape))
print ('Test data shape: {}'.format(X_test.shape))
print ('Training/Valid target shape: {}'.format(y_train_valid.shape))
print ('Test target shape: {}'.format(y_test.shape))
print ('Person train/valid shape: {}'.format(person_train_valid.shape))
print ('Person test shape: {}'.format(person_test.shape))

Training/Valid data shape: (2115, 22, 1000)
Test data shape: (443, 22, 1000)
Training/Valid target shape: (2115,)
Test target shape: (443,)
Person train/valid shape: (2115, 1)
Person test shape: (443, 1)


In [5]:
X_train_valid = X_train_valid[:, np.newaxis, :, :]
X_test = X_test[:, np.newaxis, :, :]

In [6]:
X_train_valid = torch.from_numpy(X_train_valid).float()
y_train_valid = torch.from_numpy(y_train_valid).long()
X_test = torch.from_numpy(X_test).float()
y_test = torch.from_numpy(y_test).long()

train_valid_dataset = TensorDataset(X_train_valid, y_train_valid)
test_dataset = TensorDataset(X_test, y_test)

# Splitting the dataset into train and valid sets
num_train = int(0.8 * len(train_valid_dataset))
num_valid = len(train_valid_dataset) - num_train
train_indices, valid_indices = random_split(range(len(train_valid_dataset)), [num_train, num_valid])

train_dataset = Subset(train_valid_dataset, train_indices)
valid_dataset = Subset(train_valid_dataset, valid_indices)


# Wrapping datasets with GaussianNoisyDataset
train_dataset_noisy = GaussianNoisyDataset(train_dataset, mean=0., std=1.)
valid_dataset_noisy = GaussianNoisyDataset(valid_dataset, mean=0., std=1.)
test_dataset_noisy = GaussianNoisyDataset(test_dataset, mean=0., std=1.)

batch_size = 32
train_loader = DataLoader(train_dataset_noisy, batch_size=batch_size, shuffle=True)
valid_loader = DataLoader(valid_dataset_noisy, batch_size=batch_size, shuffle=False)
test_loader = DataLoader(test_dataset_noisy, batch_size=batch_size, shuffle=False)

print('Training/Valid data shape:', X_train_valid.shape)
print('Test data shape:', X_test.shape)

Training/Valid data shape: torch.Size([2115, 1, 22, 1000])
Test data shape: torch.Size([443, 1, 22, 1000])


In [7]:
time = datetime.now().strftime("%Y-%m-%d_%H-%M-%S")
writer = SummaryWriter(f'runs/ConvNet+{time}')
model = ConvNet().to(device)

criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr = 0.001, betas=(0.9, 0.99), eps=1e-6, weight_decay=0.0005)

train(model, train_loader, valid_loader, criterion, optimizer, device=device, writer=writer, epochs=50)

test_accuracy = evaluate(model, test_loader, device=device)
print(f'Test Accuracy: {test_accuracy:.2f}%')
writer.add_scalar('test_accuracy',test_accuracy)
writer.close()

 20%|██        | 10/50 [00:14<00:55,  1.38s/it]

Epoch [10/50], Loss: 0.5411, Validation Accuracy: 55.08%


 40%|████      | 20/50 [00:27<00:41,  1.38s/it]

Epoch [20/50], Loss: 0.2410, Validation Accuracy: 49.88%


 52%|█████▏    | 26/50 [00:37<00:34,  1.45s/it]

Early stopping!
Test Accuracy: 49.89%


In [ ]:
time = datetime.now().strftime("%Y-%m-%d_%H-%M-%S")
writer = SummaryWriter(f'runs/LSTM+{time}')
lstm = LSTMModel()
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(lstm.parameters(), lr = 0.001, betas=(0.9, 0.99), eps=1e-6, weight_decay=0.0005)

lstm = lstm.to(device)
train(lstm, train_loader, valid_loader, criterion, optimizer, writer=writer, device=device)

test_accuracy = evaluate(lstm, test_loader, device=device)
print(f'Test Accuracy: {test_accuracy:.2f}%')

In [8]:
time = datetime.now().strftime("%Y-%m-%d_%H-%M-%S")
writer = SummaryWriter(f'runs/EEG+{time}')
eegn = EEGNet()
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(eegn.parameters(), lr = 0.001, betas=(0.9, 0.99),  eps=1e-7, weight_decay=0.0005)

eegn = eegn.to(device)
train(eegn, train_loader, valid_loader, criterion, optimizer, device=device, writer=writer, epochs=200)

test_accuracy = evaluate(eegn, test_loader, device=device)
print(f'Test Accuracy: {test_accuracy:.2f}%')

  0%|          | 0/200 [00:00<?, ?it/s]

  5%|▌         | 10/200 [00:12<03:55,  1.24s/it]

Epoch [10/200], Loss: 0.9428, Validation Accuracy: 59.57%


 10%|█         | 20/200 [00:25<03:44,  1.25s/it]

Epoch [20/200], Loss: 0.8389, Validation Accuracy: 61.70%


...

Epoch [110/200], Loss: 0.5157, Validation Accuracy: 70.21%


 60%|██████    | 120/200 [02:29<01:42,  1.29s/it]

Epoch [120/200], Loss: 0.5341, Validation Accuracy: 69.50%


 62%|██████▎   | 125/200 [02:37<01:34,  1.26s/it]

Early stopping!
Test Accuracy: 73.36%


In [ ]:
time = datetime.now().strftime("%Y-%m-%d_%H-%M-%S")
writer = SummaryWriter(f'runs/CNN_LSTM+{time}')
cnn_lstm = CNN_LSTM()
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(cnn_lstm.parameters(), lr = 0.001, betas=(0.9, 0.99), eps=1e-6)

cnn_lstm = cnn_lstm.to(device)
train(cnn_lstm, train_loader, valid_loader, criterion, optimizer, writer=writer, device=device, epochs=50)

test_accuracy = evaluate(cnn_lstm, test_loader, device=device)
print(f'Test Accuracy: {test_accuracy:.2f}%')

In [8]:
time = datetime.now().strftime("%Y-%m-%d_%H-%M-%S")
writer = SummaryWriter(f'runs/UltimateConvNet+{time}')
ult_cnn = UltimateConvNet()
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(ult_cnn.parameters(), lr = 0.001, betas=(0.9, 0.99), eps=1e-6, weight_decay=0.0005)

ult_cnn = ult_cnn.to(device)
train(ult_cnn, train_loader, valid_loader, criterion, optimizer, device=device, writer=writer, epochs=200)

test_accuracy = evaluate(ult_cnn, test_loader, device=device)
print(f'Test Accuracy: {test_accuracy:.2f}%')
writer.add_scalar('test_accuracy',test_accuracy)
writer.close()

  0%|          | 0/200 [00:00<?, ?it/s]


RuntimeError: mat1 and mat2 shapes cannot be multiplied (32x736 and 768x64)

In [11]:
# utilize ray tune to find best hyperparameters
import ray
from ray import tune
from ray import train as raytrain
from ray.tune import CLIReporter
from ray.tune.schedulers import ASHAScheduler
from src.methods_ray import train_ray_Ultimateconfig

config = {
    'lr': tune.loguniform(1e-4, 1e-2),
    'weight_decay': tune.loguniform(1e-4, 1e-3)
}

# Initialize Ray Tune
ray.shutdown()
ray.init()
scheduler = ASHAScheduler(metric='loss', mode='min')
reporter = CLIReporter(metric_columns=['loss'])

# Execute the hyperparameter search
analysis = tune.run(
    train_ray_Ultimateconfig,
    resources_per_trial={'gpu': 1},  # If you want to use GPUs, you can set {'gpu': 1} instead
    config=config,
    num_samples=100,
    scheduler=scheduler,
    progress_reporter=reporter
)

# Get the best hyperparameters
best_config = analysis.get_best_config(metric='loss', mode='min')
print('Best hyperparameters found are: ', best_config)

# get best accuracy using tune config


c:\Users\pluto\anaconda3\envs\kaggle\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
2024-03-11 21:10:04,927	INFO util.py:154 -- Missing packages: ['ipywidgets']. Run `pip install -U ipywidgets`, then restart the notebook server for rich notebook output.
2024-03-11 21:10:05,307	INFO util.py:154 -- Missing packages: ['ipywidgets']. Run `pip install -U ipywidgets`, then restart the notebook server for rich notebook output.
2024-03-11 21:10:07,297	ERROR services.py:1329 -- Failed to start the dashboard , return code 1
2024-03-11 21:10:07,299	ERROR services.py:1354 -- Error should be written to 'dashboard.log' or 'dashboard.err'. We are printing the last 20 lines for you. See 'https://docs.ray.io/en/master/ray-observability/ray-logging.html#logging-directory-structure' to find where the log file is.
2024-03-11 21:10:0

== Status ==
Current time: 2024-03-11 21:10:09 (running for 00:00:00.30)
Using AsyncHyperBand: num_stopped=0
Bracket: Iter 64.000: None | Iter 16.000: None | Iter 4.000: None | Iter 1.000: None
Logical resource usage: 0/16 CPUs, 0/1 GPUs (0.0/1.0 accelerator_type:G)
Result logdir: C:/Users/pluto/ray_results/train_ray_Ultimateconfig_2024-03-11_21-10-09
Number of trials: 17/100 (17 PENDING)
+--------------------------------------+----------+-------+-------------+----------------+
| Trial name                           | status   | loc   |          lr |   weight_decay |
|--------------------------------------+----------+-------+-------------+----------------|
| train_ray_Ultimateconfig_6a729_00000 | PENDING  |       | 0.000322891 |    0.000446494 |
| train_ray_Ultimateconfig_6a729_00001 | PENDING  |       | 0.00104843  |    0.000805985 |
| train_ray_Ultimateconfig_6a729_00002 | PENDING  |       | 0.000111503 |    0.00031187  |
| train_ray_Ultimateconfig_6a729_00003 | PENDING  |       | 0.

2024-03-11 21:10:24,521	ERROR tune_controller.py:1374 -- Trial task failed for trial train_ray_Ultimateconfig_6a729_00000
Traceback (most recent call last):
  File "c:\Users\pluto\anaconda3\envs\kaggle\Lib\site-packages\ray\air\execution\_internal\event_manager.py", line 110, in resolve_future
    result = ray.get(future)
             ^^^^^^^^^^^^^^^
  File "c:\Users\pluto\anaconda3\envs\kaggle\Lib\site-packages\ray\_private\auto_init_hook.py", line 22, in auto_init_wrapper
    return fn(*args, **kwargs)
           ^^^^^^^^^^^^^^^^^^^
  File "c:\Users\pluto\anaconda3\envs\kaggle\Lib\site-packages\ray\_private\client_mode_hook.py", line 103, in wrapper
    return func(*args, **kwargs)
           ^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\pluto\anaconda3\envs\kaggle\Lib\site-packages\ray\_private\worker.py", line 2626, in get
    raise value
ray.exceptions.RayActorError: The actor died unexpectedly before finishing this task.
	class_name: ImplicitFunc
	actor_id: c5a7e0bc782d63d11ae2993801000

(raylet) The node with node id: 42bf0511b2cbaa640f9880c439520434520f09731474156db8ea5dd7 and address: 127.0.0.1 and node name: 127.0.0.1 has been marked dead because the detector has missed too many heartbeats from it. This can happen when a 	(1) raylet crashes unexpectedly (OOM, preempted node, etc.) 
	(2) raylet has lagging heartbeats due to slow network or busy workload.


2024-03-11 21:10:24,536	ERROR tune_controller.py:1374 -- Trial task failed for trial train_ray_Ultimateconfig_6a729_00010
Traceback (most recent call last):
  File "c:\Users\pluto\anaconda3\envs\kaggle\Lib\site-packages\ray\air\execution\_internal\event_manager.py", line 110, in resolve_future
    result = ray.get(future)
             ^^^^^^^^^^^^^^^
  File "c:\Users\pluto\anaconda3\envs\kaggle\Lib\site-packages\ray\_private\auto_init_hook.py", line 22, in auto_init_wrapper
    return fn(*args, **kwargs)
           ^^^^^^^^^^^^^^^^^^^
  File "c:\Users\pluto\anaconda3\envs\kaggle\Lib\site-packages\ray\_private\client_mode_hook.py", line 103, in wrapper
    return func(*args, **kwargs)
           ^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\pluto\anaconda3\envs\kaggle\Lib\site-packages\ray\_private\worker.py", line 2626, in get
    raise value
ray.exceptions.RayActorError: The actor died unexpectedly before finishing this task.
	class_name: ImplicitFunc
	actor_id: 64a83888d1b386bba660e9cf01000

...

== Status ==
Current time: 2024-03-11 22:13:17 (running for 01:03:08.32)
Using AsyncHyperBand: num_stopped=0
Bracket: Iter 64.000: None | Iter 16.000: None | Iter 4.000: None | Iter 1.000: None
Logical resource usage: 0/0 CPUs, 17.0/0 GPUs
Result logdir: C:/Users/pluto/ray_results/train_ray_Ultimateconfig_2024-03-11_21-10-09
Number of trials: 34/100 (17 ERROR, 17 PENDING)
+--------------------------------------+----------+-------+-------------+----------------+
| Trial name                           | status   | loc   |          lr |   weight_decay |
|--------------------------------------+----------+-------+-------------+----------------|
| train_ray_Ultimateconfig_6a729_00017 | PENDING  |       | 0.00254709  |    0.000224577 |
| train_ray_Ultimateconfig_6a729_00018 | PENDING  |       | 0.000120901 |    0.000365404 |
| train_ray_Ultimateconfig_6a729_00019 | PENDING  |       | 0.00243147  |    0.000146708 |
| train_ray_Ultimateconfig_6a729_00020 | PENDING  |       | 0.000526361 |    0.

2024-03-11 22:13:20,398	WARNING tune.py:186 -- Stop signal received (e.g. via SIGINT/Ctrl+C), ending Ray Tune run. This will try to checkpoint the experiment state one last time. Press CTRL+C (or send SIGINT/SIGKILL/SIGTERM) to skip. 
2024-03-11 22:13:20,419	WARNING resource_updater.py:262 -- Cluster resources not detected or are 0. Attempt #2...
2024-03-11 22:13:20,923	WARNING resource_updater.py:262 -- Cluster resources not detected or are 0. Attempt #3...
2024-03-11 22:13:21,427	WARNING resource_updater.py:262 -- Cluster resources not detected or are 0. Attempt #4...
2024-03-11 22:13:21,928	WARNING resource_updater.py:262 -- Cluster resources not detected or are 0. Attempt #5...
2024-03-11 22:13:22,431	WARNING resource_updater.py:275 -- Cluster resources cannot be detected or are 0. You can resume this experiment by passing in `resume=True` to `run`.


== Status ==
Current time: 2024-03-11 22:13:22 (running for 01:03:12.99)
Using AsyncHyperBand: num_stopped=0
Bracket: Iter 64.000: None | Iter 16.000: None | Iter 4.000: None | Iter 1.000: None
Logical resource usage: 0/0 CPUs, 17.0/0 GPUs
Result logdir: C:/Users/pluto/ray_results/train_ray_Ultimateconfig_2024-03-11_21-10-09
Number of trials: 34/100 (17 ERROR, 17 PENDING)
+--------------------------------------+----------+-------+-------------+----------------+
| Trial name                           | status   | loc   |          lr |   weight_decay |
|--------------------------------------+----------+-------+-------------+----------------|
| train_ray_Ultimateconfig_6a729_00017 | PENDING  |       | 0.00254709  |    0.000224577 |
| train_ray_Ultimateconfig_6a729_00018 | PENDING  |       | 0.000120901 |    0.000365404 |
| train_ray_Ultimateconfig_6a729_00019 | PENDING  |       | 0.00243147  |    0.000146708 |
| train_ray_Ultimateconfig_6a729_00020 | PENDING  |       | 0.000526361 |    0.

2024-03-11 22:13:32,565	ERROR tune.py:1038 -- Trials did not complete: [train_ray_Ultimateconfig_6a729_00000, train_ray_Ultimateconfig_6a729_00001, train_ray_Ultimateconfig_6a729_00002, train_ray_Ultimateconfig_6a729_00003, train_ray_Ultimateconfig_6a729_00004, train_ray_Ultimateconfig_6a729_00005, train_ray_Ultimateconfig_6a729_00006, train_ray_Ultimateconfig_6a729_00007, train_ray_Ultimateconfig_6a729_00008, train_ray_Ultimateconfig_6a729_00009, train_ray_Ultimateconfig_6a729_00010, train_ray_Ultimateconfig_6a729_00011, train_ray_Ultimateconfig_6a729_00012, train_ray_Ultimateconfig_6a729_00013, train_ray_Ultimateconfig_6a729_00014, train_ray_Ultimateconfig_6a729_00015, train_ray_Ultimateconfig_6a729_00016]
2024-03-11 22:13:32,565	INFO tune.py:1042 -- Total run time: 3803.14 seconds (3790.96 seconds for the tuning loop).
2024-03-11 22:13:32,566	WARNING tune.py:1057 -- Experiment has been interrupted, but the most recent state was saved.
Resume experiment with: tune.run(..., resume=Tru

Best hyperparameters found are:  None


In [ ]:
# run with best hyperparameters
ult_cnn = UltimateConvNet()
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(ult_cnn.parameters(), lr = best_config['lr'].real, betas=(0.9, 0.99), eps=1e-6, weight_decay=best_config['weight_decay'].real)

ult_cnn = ult_cnn.to(device)
train(ult_cnn, train_loader, valid_loader, criterion, optimizer, device=device, epochs=100,patience=100)

test_accuracy = evaluate(ult_cnn, test_loader, device=device)
print(f'Test Accuracy: {test_accuracy:.2f}%')

In [ ]:
import ray
from ray import tune
from ray import train as raytrain
from ray.tune import CLIReporter
from ray.tune.schedulers import ASHAScheduler
from src.methods_ray import train_ray_Ultimateconfig
from ray.tune.search.bayesopt import BayesOptSearch
ray.shutdown()
ray.init()
scheduler = ASHAScheduler(metric='loss', mode='min', max_t= 250)
reporter = CLIReporter(metric_columns=['loss'])
bayesopt = BayesOptSearch(
    metric='loss',
    mode='min',
)

# config = {
#     'weight_decay': tune.loguniform(1e-4, 1e-3),
# }

config = {
    'lr': tune.loguniform(1e-4, 1e-2),
}


analysis = tune.run(
    train_ray_Ultimateconfig,
    resources_per_trial={'gpu': 1},  # If you want to use GPUs, you can set {'gpu': 1} instead
    config=config,
    num_samples=20,
    search_alg=bayesopt,
    scheduler=scheduler,
    progress_reporter=reporter
)

# Get the best hyperparameters
best_config = analysis.get_best_config(metric='loss', mode='min')
print('Best hyperparameters found are: ', best_config)

In [ ]:
dfs = analysis.trial_dataframes
import matplotlib.pyplot as plt

for d in dfs.values():
    # TODO: Plot the results
    plt.plot(d['training_iteration'], d['loss'], label=d['config/weight_decay'][0])

plt.xlabel('Iterations')
plt.ylabel('Loss')
plt.title('Trial Progress Over Time')
plt.show()

In [ ]:
# run with best hyperparameters
ult_cnn = UltimateConvNet()
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(ult_cnn.parameters(), lr = 0.00734, betas=(0.9, 0.99), eps=1e-6, weight_decay=0.0004370)

ult_cnn = ult_cnn.to(device)
train(ult_cnn, train_loader, valid_loader, criterion, optimizer, device=device, epochs=200,patience=40)

test_accuracy = evaluate(ult_cnn, test_loader, device=device)
print(f'Test Accuracy: {test_accuracy:.2f}%')

In [ ]:
vit = ViT(patch_size=(22, 1), num_classes=4, dim=64, num_head=8, num_layers = 2)
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.SGD(vit.parameters(), lr=0.01, momentum=0.9)

vit = vit.to(device)
train(vit, train_loader, valid_loader, criterion, optimizer, device=device, epochs=200)

test_accuracy = evaluate(vit, test_loader, device=device)
print(f'Test Accuracy: {test_accuracy:.2f}%')

In [ ]:
eegn = EEGNet_Modified()
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(eegn.parameters(), lr = 0.001, betas=(0.9, 0.99), eps=1e-7, weight_decay=0.0005)

eegn = eegn.to(device)
train(eegn, train_loader, valid_loader, criterion, optimizer, device=device, epochs=100)

test_accuracy = evaluate(eegn, test_loader, device=device)
print(f'Test Accuracy: {test_accuracy:.2f}%')